In [15]:
import json

# Open the JSONL file
file = open('hotpotqa-dev-kilt.jsonl', 'r')

hotpotqa_dataset = []

# Read the JSONL file line by line and parse each line as JSON
for line in file:
    data = json.loads(line)
    hotpotqa_dataset.append(data)

# Checking Dataset Structure


In [16]:
# Iterate over the dataset and count the frequency of each output
for data in hotpotqa_dataset:
    output = []
    for datapoint in data['output']:
        if "provenance" not in datapoint or len(datapoint["provenance"]) > 1:
            print(datapoint)

{'answer': 'yes', 'provenance': [{'wikipedia_id': '2816539', 'title': 'Scott Derrickson', 'start_paragraph_id': 1, 'start_character': 0, 'end_paragraph_id': 1, 'end_character': 81, 'bleu_score': 0.6964705665515707, 'section': 'Section::::Abstract.'}, {'wikipedia_id': '10520', 'title': 'Ed Wood', 'start_paragraph_id': 1, 'start_character': 0, 'end_paragraph_id': 1, 'end_character': 106, 'bleu_score': 0.7784290264326612, 'section': 'Section::::Abstract.'}]}
{'answer': 'Chief of Protocol', 'provenance': [{'wikipedia_id': '33022480', 'title': 'Kiss and Tell (1945 film)', 'start_paragraph_id': 1, 'start_character': 0, 'end_paragraph_id': 1, 'end_character': 104, 'bleu_score': 1.0, 'section': 'Section::::Abstract.'}, {'wikipedia_id': '804602', 'title': 'Shirley Temple', 'start_paragraph_id': 1, 'start_character': 0, 'end_paragraph_id': 1, 'end_character': 211, 'bleu_score': 1.0, 'section': 'Section::::Abstract.'}, {'wikipedia_id': '804602', 'title': 'Shirley Temple', 'start_paragraph_id': 1,

# Filtering Data

In [17]:
filtered_hotpotqa_dataset = {}
numberOfDatapoints = 0
documentFrequency = {}

# Iterate over the dataset and count the frequency of each output
for data in hotpotqa_dataset:
    content = {}
    flag = 0
    content["input"] = data['input']
    content["output"] = {}
    for datapoint in data['output']:
        # Avoid datapoints with missing features
        if "provenance" in datapoint and "answer" in datapoint and len(datapoint["provenance"]) > 0:
            flag = 1
            if(datapoint["provenance"][0]["wikipedia_id"] in content["output"]):
                content["output"][datapoint["provenance"][0]["wikipedia_id"]].append(datapoint["answer"])
            else:
                content["output"][datapoint["provenance"][0]["wikipedia_id"]] = [datapoint["answer"]]
    
    # No Empty output
    if(len(content["output"]) != 0):
        filtered_hotpotqa_dataset[data['id']] = content
        numberOfDatapoints += flag
        if len(content["output"]) in documentFrequency:
            documentFrequency[len(content["output"])] += 1
        else:
            documentFrequency[len(content["output"])] = 1
        if(len(content["output"]) == 0):
            print(content)

In [18]:
len(filtered_hotpotqa_dataset), numberOfDatapoints, documentFrequency

(5600, 5600, {1: 5600})

In [19]:
print(json.dumps(filtered_hotpotqa_dataset, indent=4))

{
    "5a8b57f25542995d1e6f1371": {
        "input": "Were Scott Derrickson and Ed Wood of the same nationality?",
        "output": {
            "2816539": [
                "yes"
            ]
        }
    },
    "5a8c7595554299585d9e36b6": {
        "input": "What government position was held by the woman who portrayed Corliss Archer in the film Kiss and Tell?",
        "output": {
            "33022480": [
                "Chief of Protocol"
            ]
        }
    },
    "5a85ea095542994775f606a8": {
        "input": "What science fantasy young adult series, told in first person, has a set of companion books narrating the stories of enslaved worlds and alien species?",
        "output": {
            "12342237": [
                "Animorphs"
            ]
        }
    },
    "5adbf0a255429947ff17385a": {
        "input": "Are the Laleli Mosque and Esma Sultan Mansion located in the same neighborhood?",
        "output": {
            "9421721": [
                "no"
      

In [20]:
# Take the first 1500 datapoints from filtered_eli5_dataset
filtered_hotpotqa_dataset_first_1500 = dict(list(filtered_hotpotqa_dataset.items())[:2100])

# Print the length to verify
print(len(filtered_hotpotqa_dataset_first_1500))

2100


In [21]:
# Save data to a JSON file
with open('data2.json', 'w') as json_file:
    json.dump(filtered_hotpotqa_dataset_first_1500, json_file, indent=4)